In [1]:
import json
import copy
import pandas as pd

In [84]:
# ingr = None
# with open("ingr2m.json", "r") as f:
#     ingr = json.load(f)

In [2]:
newdf = pd.read_parquet("ingr1650k.gzip")

In [8]:
ingr10 = ["; ".join(i) for i in newdf.sample(10, random_state=28394).ingr.tolist()]
df10 = pd.DataFrame({'ingr':ingr10})
df10.to_csv('../../data/reportdata_ib.csv')

In [86]:
ingr = newdf.ingr.tolist()

In [87]:
def is_number(s):
    try:
        float(s)
        return True
    except ValueError:
        return False

In [88]:
ingr10w = ingr[100000:200000]
ingr500k = ingr[:500000]

In [89]:
omitted = []
def ingr_process(ingredients):
    ingr_ = []
    for i in ingredients:
        append_switch = True
        ingr_t= []
        for j in range(len(i)):
            temp = i[j].split()
            if "-" in temp[0]:
                num_split = temp[0].split("-")
                try:
                    if not(is_number(num_split[-1])):
                        # if len(num_split) == 2:
                        #     temp = num_split+temp[1:]
                        if len(num_split) == 3 and is_number(num_split[0]):
                            # print(temp)
                            # num_split = [float(num) for num in num_split[:2]]
                            temp = [str(round((float(num_split[0])+float(num_split[1]))/2,2)), num_split[-1]] + temp[1:]
                            # print(temp)
                            # raise KeyError
                        else:
                            temp = num_split+temp[1:]
                    elif is_number(num_split[0]):
                            num_split = [float(num) for num in num_split]
                            temp[0] = str(round((num_split[0]+num_split[1])/2,2))
                except:
                    print(num_split, temp)
                    omitted.append(i)
                    append_switch = False
                    break
                    # raise ValueError("sth is wrong")
            ingr_t.append((temp))
        if append_switch:
            ingr_.append(ingr_t)
    return ingr_
# ingr_
        

In [90]:
ingr_ = ingr_process(ingr10w)
masked_ingr = []
tag = []
for i in range(len(ingr_)):
    temp = []
    temp_tag = []
    for j in range(len(ingr_[i])):
        c = copy.deepcopy(ingr_[i])
        # print(c)
        if not is_number(c[j][0]):
            continue
        else:
            # print(c[j][0])
            temp_tag.append(c[j][0])
            c[j][0] = "[MASK]"
            temp.append([" ".join(s) for s in c])
    masked_ingr.append(temp)
    tag.append(temp_tag)
# masked_ingr

['2', '', ''] ['2--', '8', 'oz', 'package', 'cream', 'cheese']


In [92]:
ingr_400 = []
tag_400 = []
for i in range(len(masked_ingr)):
    recipe_group = []
    tag_group = []
    for j in range(len(masked_ingr[i])):
        temp = "; ".join(masked_ingr[i][j])
        if not len(temp) > 400:
            recipe_group.append(temp)
            tag_group.append(float(tag[i][j]))
    if recipe_group:
        ingr_400.append(recipe_group)
        tag_400.append(tag_group)

In [93]:
for i, j in zip(ingr_400, tag_400):
    if len(i)!=len(j):
        print("no")

In [94]:
# import pandas as pd
df = pd.DataFrame({'ingr':ingr_400 ,'tags':tag_400})

In [95]:
df.iloc[30][1]

[3.0, 1.0, 6.0, 2.0, 1.0, 0.5]

In [96]:
df.to_parquet("ingr10w_masked_grouped.gzip", index=False, compression="gzip")

In [14]:
newdf = pd.read_parquet("ingr10w_masked_grouped.gzip")
newdf

array(['[MASK] c. onion; 0.75 c. celery; garlic; 6 c. water; 1 (28 oz.) can cut up tomatoes; 0.75 c. lentils; 0.75 c. barley; vegetarian bouillon cubes; 0.5 tsp. dried rosemary; 0.5 tsp. oregano; 0.25 tsp. pepper; 1 c. carrots',
       '0.75 c. onion; [MASK] c. celery; garlic; 6 c. water; 1 (28 oz.) can cut up tomatoes; 0.75 c. lentils; 0.75 c. barley; vegetarian bouillon cubes; 0.5 tsp. dried rosemary; 0.5 tsp. oregano; 0.25 tsp. pepper; 1 c. carrots',
       '0.75 c. onion; 0.75 c. celery; garlic; [MASK] c. water; 1 (28 oz.) can cut up tomatoes; 0.75 c. lentils; 0.75 c. barley; vegetarian bouillon cubes; 0.5 tsp. dried rosemary; 0.5 tsp. oregano; 0.25 tsp. pepper; 1 c. carrots',
       '0.75 c. onion; 0.75 c. celery; garlic; 6 c. water; [MASK] (28 oz.) can cut up tomatoes; 0.75 c. lentils; 0.75 c. barley; vegetarian bouillon cubes; 0.5 tsp. dried rosemary; 0.5 tsp. oregano; 0.25 tsp. pepper; 1 c. carrots',
       '0.75 c. onion; 0.75 c. celery; garlic; 6 c. water; 1 (28 oz.) can cut 

In [17]:
ingr10w400 = [", ".join(i) for i in ingr10w if len(", ".join(i)) <= 400]

# miv

In [97]:
tingr = copy.deepcopy(ingr500k[:int(len(ingr500k)/2)])
fingr = copy.deepcopy(ingr500k[int(len(ingr500k)/2):])

In [98]:
out = ingr_process(fingr)

['2', '', '', '8'] ['2---8', 'oz.', 'cream', 'cheese']
['2', '1/2', '3'] ['2-1/2-3', 'c.', 'shredded', 'cabbage']
['2', '', ''] ['2--', '8', 'oz.', 'cream', 'cheese']


In [99]:
import numpy as np
out_len = [len(o) for o in out]
np.average(out_len)

7.469561634739617

In [100]:
out_filtered = []
for o in out[:]:
    num_ingr = len(o)
    for i in o:
        if not(is_number(i[0])):
            print(i)
            num_ingr -= 1
    if num_ingr > 0:
        out_filtered.append(o)
print(len(out), len(out_filtered))

['onion,', 'salt', 'and', 'pepper', 'to', 'taste']
['tortillas']
['Cheddar', 'cheese,', 'grated']
['dash', 'of', 'butter', 'salt']
['bread', 'or', 'rice', 'stuffing']
['salt', 'and', 'pepper', 'to', 'taste']
['vanilla', 'wafers']
['strawberries']
['any', 'other', 'fruit', 'you', 'want']
['sliced', 'ripe', 'olives,', 'cut', 'in', 'half', '(optional)']
['parsley', 'sprigs', '(optional)']
['cooking', 'oil']
['soy', 'sauce']
['dash', 'of', 'basil', 'and', 'oregano']
['salt', 'and', 'pepper']
["Cavender's", 'Greek', 'Seasoning']
['oil', 'for', 'frying']
['salt', 'and', 'pepper', 'to', 'taste']
['chopped', 'nuts', '(optional)']
['salt', 'and', 'pepper', 'to', 'taste']
['salt', 'and', 'pepper']
['Flavored', 'Carbonated', 'Beverage']
['dash', 'of', 'salt']
['grated', 'cheese', '(Monterey', 'Jack', 'and', 'others;', 'I', 'use', '3', 'cheeses,', 'Monterey', 'Jack,', 'Mozzarella', 'and', 'Cheddar)']
['salt', 'to', 'taste']
['sugar', 'to', 'taste']
['pepper', 'to', 'taste']
['bacon', 'bits', '(8',

In [101]:
import random
random.seed(999)
progress = 0
for i in range(len(out_filtered)):
    randomized = False
    progress += 1
    print(progress, end = '\r')
    while randomized == False:
        for j in range(len(out_filtered[i])):
            if is_number(out_filtered[i][j][0]) and random.randint(1,4) == 1:
                randomized = True
                out_filtered[i][j][0] = str(round(float(out_filtered[i][j][0])*random.randint(0,20)*0.2, 2))

In [71]:
out_filtered

[[['25.92', 'cans', 'tuna,', 'flaked'],
  ['0.5', 'c.', 'sour', 'cream'],
  ['0.5', 'c.', 'cornflake', 'crumbs'],
  ['0.5', 'c.', 'milk'],
  ['2', 'eggs,', 'well', 'beaten'],
  ['1.32', 'c.', 'margarine'],
  ['2', 'grated', 'carrots'],
  ['2.0', 'c.', 'frozen', 'peas'],
  ['onion,', 'salt', 'and', 'pepper', 'to', 'taste']],
 [['1.5', 'lb.', 'ground', 'beef'],
  ['1.6', 'small', 'onion'],
  ['1', 'can', 'cream', 'of', 'mushroom', 'soup'],
  ['1', 'can', 'cream', 'of', 'chicken', 'soup'],
  ['1.6', 'c.', 'milk'],
  ['1.6', 'small', 'can', 'Las', 'Palmas', 'red', 'chili', 'sauce'],
  ['1.2', 'small', 'can', 'diced', 'Ortega', 'peppers'],
  ['1', 'small', 'can', 'chopped', 'olives'],
  ['tortillas'],
  ['Cheddar', 'cheese,', 'grated']],
 [['0.4', 'c.', 'butter', 'or', 'margarine'],
  ['9.6', 'oz.', 'pkg.', 'cream', 'cheese'],
  ['1', 'c.', 'powdered', 'sugar'],
  ['6.8', '(4', 'oz.)', 'pkg.', 'chocolate', 'instant', 'pudding'],
  ['3.5', 'c.', 'milk'],
  ['12', 'oz.', 'Cool', 'Whip'],
  ['

In [102]:
ingr_f = ["; ".join([" ".join(j) for j in i]) for i in out_filtered]
ingr_t = ["; ".join([" ".join(j) for j in i]) for i in ingr_process(tingr)]

['1', '1/2', 'lbs'] ['1-1/2-lbs', 'or', '7', 'med.', 'baking', 'potatoes,', 'peeled', 'and', 'cut', 'into', 'thin', 'wedges', 'or', 'strips']
['1', '', '', '32'] ['1---32', 'oz', 'tomato', 'sauce']
['2', '', ''] ['2--', '8', 'oz', 'package', 'cream', 'cheese']


In [82]:
# " ".join(['2--', '8', 'oz', 'package', 'cream', 'cheese'])
# # " ".join(['1---32', 'oz', 'tomato', 'sauce'])

'2-- 8 oz package cream cheese'

In [103]:
ingr_f = [i for i in ingr_f if len(i) <= 400]
ingr_t = [i for i in ingr_t if len(i) <= 400]

In [104]:
def balance(l1, l2):
    length = 0
    if len(l1) > len(l2):
        length = len(l2)
    else:
        length = len(l1)
    return l1[:length], l2[:length], length

In [105]:
i_t, i_f, i_len = balance(ingr_t, ingr_f)
tftag = [[1,0]]*i_len + [[0,1]]*i_len
# ftag = [[0,1]]*i_len
i_tf = i_t + i_f
# print(len(i_t),len(i_f))
# df_t = pd.DataFrame({'ingr':i_t,'tags':ttag})
# df_f = pd.DataFrame({'ingr':i_f,'tags':ftag})
df_b = pd.DataFrame({'ingr':i_tf,'tags':tftag})
df_b

ingr    tags
0       1 c. firmly packed brown sugar, 0.5 c. evapora...  [1, 0]
1       1 small jar chipped beef, cut up, 4 boned chic...  [1, 0]
2       2 (16 oz.) pkg. frozen corn, 1 (8 oz.) pkg. cr...  [1, 0]
3       1 large whole chicken, 2 (10.5 oz.) cans chick...  [1, 0]
4       1 c. peanut butter, 0.75 c. graham cracker cru...  [1, 0]
...                                                   ...     ...
492131  1 bag fresh cranberries, 1.5 c. sugar, 2.6 c. ...  [0, 1]
492132  4 c. diced apples, 1 c. whole cranberries, 1.6...  [0, 1]
492133  7.6 lb. hamburger, sliced cheese, 1 can cream ...  [0, 1]
492134  3.2 c. chopped onions, 0.25 c. green pepper, 2...  [0, 1]
492135  1 c. shortening or oleo, 0.8 eggs, 2 tsp. vani...  [0, 1]

[492136 rows x 2 columns]

In [106]:
df_b.to_parquet("ingr500k_bool.gzip", index=False, compression='gzip')

In [1]:
import pandas as pd

In [5]:
testdf = pd.read_parquet('ingr10w_masked_grouped.gzip')
testdf2 = pd.read_parquet('./test/ingr10w_masked_grouped.gzip')

In [6]:
testdf

ingr  \
0      [[MASK] c. onion; 0.75 c. celery; garlic; 6 c....   
1      [[MASK] large red tomatoes; 0.25 c. salad oil;...   
2      [[MASK] lb. hamburg, browned; 0.5 c. chopped o...   
3      [[MASK] zucchini squash; 4 yellow squash; 1 la...   
4      [[MASK] box lemon cake mix; 1 box pineapple in...   
...                                                  ...   
98472  [[MASK] cake wax, melted in small pan; 0.5 c. ...   
98473  [[MASK] lb. chopped meat; 1 small onion, chopp...   
98474  [[MASK] (8 oz.) pkg. cream cheese; 0.5 c. Hell...   
98475  [[MASK] boneless, skinless chicken breasts; 1 ...   
98476  [[MASK] c. plain yogurt; 2 c. cucumber peeled,...   

                                                    tags  
0      [0.75, 0.75, 6.0, 1.0, 0.75, 0.75, 0.5, 0.5, 0...  
1                        [4.0, 0.25, 1.0, 0.5, 0.5, 0.5]  
2                    [1.0, 0.5, 1.0, 1.0, 1.0, 0.5, 1.5]  
3                              [3.0, 4.0, 1.0, 1.0, 1.0]  
4                             [1.0, 1.0, 4.0, 0.75, 1.0]  
...                                                  ...  
98472                     [0.5, 0.5, 1.5, 1.5, 1.0, 2.0]  
98473                               [1.5, 1.0, 2.0, 0.5]  
98474                               [1.0, 0.5, 0.5, 1.0]  
98475                               [4.0, 1.0, 3.0, 1.0]  
98476                    [4.0, 2.0, 0.75, 2.0, 1.0, 0.5]  

[98477 rows x 2 columns]

In [9]:
testdf2

ingr  \
0      [[MASK] c. onion; 0.75 c. celery; garlic; 6 c....   
1      [[MASK] large red tomatoes; 0.25 c. salad oil;...   
2      [[MASK] lb. hamburg, browned; 0.5 c. chopped o...   
3      [[MASK] zucchini squash; 4 yellow squash; 1 la...   
4      [[MASK] box lemon cake mix; 1 box pineapple in...   
...                                                  ...   
98473  [[MASK] cake wax, melted in small pan; 0.5 c. ...   
98474  [[MASK] lb. chopped meat; 1 small onion, chopp...   
98475  [[MASK] (8 oz.) pkg. cream cheese; 0.5 c. Hell...   
98476  [[MASK] boneless, skinless chicken breasts; 1 ...   
98477  [[MASK] c. plain yogurt; 2 c. cucumber peeled,...   

                                                    tags  
0      [0.75, 0.75, 6.0, 1.0, 0.75, 0.75, 0.5, 0.5, 0...  
1                        [4.0, 0.25, 1.0, 0.5, 0.5, 0.5]  
2                    [1.0, 0.5, 1.0, 1.0, 1.0, 0.5, 1.5]  
3                              [3.0, 4.0, 1.0, 1.0, 1.0]  
4                             [1.0, 1.0, 4.0, 0.75, 1.0]  
...                                                  ...  
98473                     [0.5, 0.5, 1.5, 1.5, 1.0, 2.0]  
98474                               [1.5, 1.0, 2.0, 0.5]  
98475                               [1.0, 0.5, 0.5, 1.0]  
98476                               [4.0, 1.0, 3.0, 1.0]  
98477                    [4.0, 2.0, 0.75, 2.0, 1.0, 0.5]  

[98478 rows x 2 columns]